In [9]:
#import autograd.numpy as np

class Scheduler:
    """
    Abstract class for Schedulers
    """

    def __init__(self, eta):
        self.eta = eta

    # should be overwritten
    def update_change(self, gradient):
        raise NotImplementedError

    # overwritten if needed
    def reset(self):
        pass


class Constant(Scheduler):
    def __init__(self, eta):
        super().__init__(eta)

    def update_change(self, gradient):
        return self.eta * gradient
    
    def reset(self):
        pass


class Momentum(Scheduler):
    def __init__(self, eta: float, momentum: float):
        super().__init__(eta)
        self.momentum = momentum
        self.change = 0

    def update_change(self, gradient):
        self.change = self.momentum * self.change + self.eta * gradient
        return self.change

    def reset(self):
        pass


class Adagrad(Scheduler):
    def __init__(self, eta):
        super().__init__(eta)
        self.G_t = None

    def update_change(self, gradient):
        delta = 1e-8  # avoid division ny zero

        if self.G_t is None:
            self.G_t = npf.zeros((gradient.shape[0], gradient.shape[0]))

        self.G_t += gradient @ gradient.T

        G_t_inverse = 1 / (
            delta + npf.sqrt(npf.reshape(npf.diagonal(self.G_t), (self.G_t.shape[0], 1)))
        )
        return self.eta * gradient * G_t_inverse

    def reset(self):
        self.G_t = None


class AdagradMomentum(Scheduler):
    def __init__(self, eta, momentum):
        super().__init__(eta)
        self.G_t = None
        self.momentum = momentum
        self.change = 0

    def update_change(self, gradient):
        delta = 1e-8  # avoid division ny zero

        if self.G_t is None:
            self.G_t = npf.zeros((gradient.shape[0], gradient.shape[0]))

        self.G_t += gradient @ gradient.T

        G_t_inverse = 1 / (
            delta + npf.sqrt(npf.reshape(npf.diagonal(self.G_t), (self.G_t.shape[0], 1)))
        )
        self.change = self.change * self.momentum + self.eta * gradient * G_t_inverse
        return self.change

    def reset(self):
        self.G_t = None


class RMS_prop(Scheduler):
    def __init__(self, eta, rho):
        super().__init__(eta)
        self.rho = rho
        self.second = 0.0

    def update_change(self, gradient):
        delta = 1e-8  # avoid division ny zero
        self.second = self.rho * self.second + (1 - self.rho) * gradient * gradient
        return self.eta * gradient / (npf.sqrt(self.second + delta))

    def reset(self):
        self.second = 0.0


class Adam(Scheduler):
    def __init__(self, eta, rho, rho2):
        super().__init__(eta)
        self.rho = rho
        self.rho2 = rho2
        self.moment = 0
        self.second = 0
        self.n_epochs = 1

    def update_change(self, gradient):
        delta = 1e-8  # avoid division ny zero

        self.moment = self.rho * self.moment + (1 - self.rho) * gradient
        self.second = self.rho2 * self.second + (1 - self.rho2) * gradient * gradient

        moment_corrected = self.moment / (1 - self.rho**self.n_epochs)
        second_corrected = self.second / (1 - self.rho2**self.n_epochs)

        return self.eta * moment_corrected / (npf.sqrt(second_corrected + delta))

    def reset(self):
        self.n_epochs += 1
        self.moment = 0
        self.second = 0

In [10]:
#import autograd.numpy as np

def CostOLS(target):
    
    def func(X):
        return (1.0 / target.shape[0]) * npf.sum((target - X) ** 2)

    return func


def CostLogReg(target):

    def func(X):
        epsilon = 1e-10
        # Apply epsilon to prevent log(0) or log(1) which results in numerical instability
        X = npf.clip(X, epsilon, 1 - epsilon)
        return -(1.0 / target.shape[0]) * npf.sum(
            (target * npf.log(X)) + ((1 - target) * npf.log(1 - X))
            )      

    return func


def CostCrossEntropy(target):
    
    def func(X):
        return -(1.0 / target.size) * npf.sum(target * npf.log(X + 10e-10))

    return func

In [11]:
#import autograd.numpy as np
#from autograd import elementwise_grad

def identity(X):
    return X


def sigmoid(X):
    try:
        return 1.0 / (1 + npf.exp(-X))
    except FloatingPointError:
        return npf.where(X > npf.zeros(X.shape), npf.ones(X.shape), npf.zeros(X.shape))


def softmax(X):
    X = X - npf.max(X, axis=-1, keepdims=True)
    delta = 10e-10
    return npf.exp(X) / (npf.sum(npf.exp(X), axis=-1, keepdims=True) + delta)


def RELU(X):
    return npf.where(X > npf.zeros(X.shape), X, npf.zeros(X.shape))


def LRELU(X):
    delta = 10e-4
    return npf.where(X > npf.zeros(X.shape), X, delta * X)


def derivate(func):
    if func.__name__ == "RELU":

        def func(X):
            return npf.where(X > 0, 1, 0)

        return func

    elif func.__name__ == "LRELU":

        def func(X):
            delta = 10e-4
            return npf.where(X > 0, 1, delta)

        return func

    else:
        return elementwise_grad(func)

In [12]:
import math
import autograd.numpy as npf
import sys
import warnings
from autograd import grad, elementwise_grad
from random import random, seed
from copy import deepcopy, copy
from typing import Tuple, Callable
from sklearn.utils import resample

warnings.simplefilter("error")


class FFNN:
    """
    Description:
    ------------
        Feed Forward Neural Network with interface enabling flexible design of a
        nerual networks architecture and the specification of activation function
        in the hidden layers and output layer respectively. This model can be used
        for both regression and classification problems, depending on the output function.

    Attributes:
    ------------
        I   dimensions (tuple[int]): A list of positive integers, which specifies the
            number of nodes in each of the networks layers. The first integer in the array
            defines the number of nodes in the input layer, the second integer defines number
            of nodes in the first hidden layer and so on until the last number, which
            specifies the number of nodes in the output layer.
        II  hidden_func (Callable): The activation function for the hidden layers
        III output_func (Callable): The activation function for the output layer
        IV  cost_func (Callable): Our cost function
        V   seed (int): Sets random seed, makes results reproducible
    """

    def __init__(
        self,
        dimensions: tuple[int],
        hidden_func: Callable = sigmoid,
        output_func: Callable = lambda x: x,
        cost_func: Callable = CostOLS,
        seed: int = None,
    ):
        self.dimensions = dimensions
        self.hidden_func = hidden_func
        self.output_func = output_func
        self.cost_func = cost_func
        self.seed = seed
        self.weights = list()
        self.schedulers_weight = list()
        self.schedulers_bias = list()
        self.a_matrices = list()
        self.z_matrices = list()
        self.classification = None

        self.reset_weights()
        self._set_classification()

    def fit(
        self,
        X: npf.ndarray,
        t: npf.ndarray,
        scheduler: Scheduler,
        batches: int = 1,
        epochs: int = 100,
        lam: float = 0,
        X_val: npf.ndarray = None,
        t_val: npf.ndarray = None,
    ):
        """
        Description:
        ------------
            This function performs the training the neural network by performing the feedforward and backpropagation
            algorithm to update the networks weights.

        Parameters:
        ------------
            I    X (np.ndarray) : training data
            II   t (np.ndarray) : target data
            III  scheduler (Scheduler) : specified scheduler (algorithm for optimization of gradient descent)
            IV   scheduler_args (list[int]) : list of all arguments necessary for scheduler

        Optional Parameters:
        ------------
            V    batches (int) : number of batches the datasets are split into, default equal to 1
            VI   epochs (int) : number of iterations used to train the network, default equal to 100
            VII  lam (float) : regularization hyperparameter lambda
            VIII X_val (np.ndarray) : validation set
            IX   t_val (np.ndarray) : validation target set

        Returns:
        ------------
            I   scores (dict) : A dictionary containing the performance metrics of the model.
                The number of the metrics depends on the parameters passed to the fit-function.

        """

        # setup 
        if self.seed is not None:
            npf.random.seed(self.seed)

        val_set = False
        if X_val is not None and t_val is not None:
            val_set = True

        # creating arrays for score metrics
        train_errors = npf.empty(epochs)
        train_errors.fill(npf.nan)
        val_errors = npf.empty(epochs)
        val_errors.fill(npf.nan)

        train_accs = npf.empty(epochs)
        train_accs.fill(npf.nan)
        val_accs = npf.empty(epochs)
        val_accs.fill(npf.nan)

        self.schedulers_weight = list()
        self.schedulers_bias = list()

        batch_size = X.shape[0] // batches

        X, t = resample(X, t)

        # this function returns a function valued only at X
        cost_function_train = self.cost_func(t)
        if val_set:
            cost_function_val = self.cost_func(t_val)

        # create schedulers for each weight matrix
        for i in range(len(self.weights)):
            self.schedulers_weight.append(copy(scheduler))
            self.schedulers_bias.append(copy(scheduler))

        print(f"{scheduler.__class__.__name__}: Eta={scheduler.eta}, Lambda={lam}")

        try:
            for e in range(epochs):
                for i in range(batches):
                    # allows for minibatch gradient descent
                    if i == batches - 1:
                        # If the for loop has reached the last batch, take all thats left
                        X_batch = X[i * batch_size :, :]
                        t_batch = t[i * batch_size :, :]
                    else:
                        X_batch = X[i * batch_size : (i + 1) * batch_size, :]
                        t_batch = t[i * batch_size : (i + 1) * batch_size, :]

                    self._feedforward(X_batch)
                    self._backpropagate(X_batch, t_batch, lam)

                # reset schedulers for each epoch (some schedulers pass in this call)
                for scheduler in self.schedulers_weight:
                    scheduler.reset()

                for scheduler in self.schedulers_bias:
                    scheduler.reset()

                # computing performance metrics
                pred_train = self.predict(X)
                train_error = cost_function_train(pred_train)

                train_errors[e] = train_error
                if val_set:
                    
                    pred_val = self.predict(X_val)
                    val_error = cost_function_val(pred_val)
                    val_errors[e] = val_error

                if self.classification:
                    train_acc = self._accuracy(self.predict(X), t)
                    train_accs[e] = train_acc
                    if val_set:
                        val_acc = self._accuracy(pred_val, t_val)
                        val_accs[e] = val_acc

                # printing progress bar
                progression = e / epochs
                print_length = self._progress_bar(
                    progression,
                    train_error=train_errors[e],
                    train_acc=train_accs[e],
                    val_error=val_errors[e],
                    val_acc=val_accs[e],
                )
        except KeyboardInterrupt:
            # allows for stopping training at any point and seeing the result
            pass

        # visualization of training progression (similiar to tensorflow progression bar)
        sys.stdout.write("\r" + " " * print_length)
        sys.stdout.flush()
        self._progress_bar(
            1,
            train_error=train_errors[e],
            train_acc=train_accs[e],
            val_error=val_errors[e],
            val_acc=val_accs[e],
        )
        sys.stdout.write("")

        # return performance metrics for the entire run
        scores = dict()

        scores["train_errors"] = train_errors

        if val_set:
            scores["val_errors"] = val_errors

        if self.classification:
            scores["train_accs"] = train_accs

            if val_set:
                scores["val_accs"] = val_accs

        return scores

    def predict(self, X: npf.ndarray, *, threshold=0.5):
        """
         Description:
         ------------
             Performs prediction after training of the network has been finished.

         Parameters:
        ------------
             I   X (np.ndarray): The design matrix, with n rows of p features each

         Optional Parameters:
         ------------
             II  threshold (float) : sets minimal value for a prediction to be predicted as the positive class
                 in classification problems

         Returns:
         ------------
             I   z (np.ndarray): A prediction vector (row) for each row in our design matrix
                 This vector is thresholded if regression=False, meaning that classification results
                 in a vector of 1s and 0s, while regressions in an array of decimal numbers

        """

        predict = self._feedforward(X)

        if self.classification:
            return npf.where(predict > threshold, 1, 0)
        else:
            return predict

    def reset_weights(self):
        """
        Description:
        ------------
            Resets/Reinitializes the weights in order to train the network for a new problem.

        """
        if self.seed is not None:
            npf.random.seed(self.seed)

        self.weights = list()
        for i in range(len(self.dimensions) - 1):
            weight_array = npf.random.randn(
                self.dimensions[i] + 1, self.dimensions[i + 1]
            )
            weight_array[0, :] = npf.random.randn(self.dimensions[i + 1]) * 0.01

            self.weights.append(weight_array)

    def _feedforward(self, X: npf.ndarray):
        """
        Description:
        ------------
            Calculates the activation of each layer starting at the input and ending at the output.
            Each following activation is calculated from a weighted sum of each of the preceeding
            activations (except in the case of the input layer).

        Parameters:
        ------------
            I   X (np.ndarray): The design matrix, with n rows of p features each

        Returns:
        ------------
            I   z (np.ndarray): A prediction vector (row) for each row in our design matrix
        """

        # reset matrices
        self.a_matrices = list()
        self.z_matrices = list()

        # if X is just a vector, make it into a matrix
        if len(X.shape) == 1:
            X = X.reshape((1, X.shape[0]))

        # Add a coloumn of zeros as the first coloumn of the design matrix, in order
        # to add bias to our data
        bias = npf.ones((X.shape[0], 1)) * 0.01
        X = npf.hstack([bias, X])

        # a^0, the nodes in the input layer (one a^0 for each row in X - where the
        # exponent indicates layer number).
        a = X
        self.a_matrices.append(a)
        self.z_matrices.append(a)

        # The feed forward algorithm
        for i in range(len(self.weights)):
            if i < len(self.weights) - 1:
                z = a @ self.weights[i]
                self.z_matrices.append(z)
                a = self.hidden_func(z)
                # bias column again added to the data here
                bias = npf.ones((a.shape[0], 1)) * 0.01
                a = npf.hstack([bias, a])
                self.a_matrices.append(a)
            else:
                try:
                    # a^L, the nodes in our output layers
                    z = a @ self.weights[i]
                    a = self.output_func(z)
                    self.a_matrices.append(a)
                    self.z_matrices.append(z)
                except Exception as OverflowError:
                    print(
                        "OverflowError in fit() in FFNN\nHOW TO DEBUG ERROR: Consider lowering your learning rate or scheduler specific parameters such as momentum, or check if your input values need scaling"
                    )

        # this will be a^L
        return a

    def _backpropagate(self, X, t, lam):
        """
        Description:
        ------------
            Performs the backpropagation algorithm. In other words, this method
            calculates the gradient of all the layers starting at the
            output layer, and moving from right to left accumulates the gradient until
            the input layer is reached. Each layers respective weights are updated while
            the algorithm propagates backwards from the output layer (auto-differentation in reverse mode).

        Parameters:
        ------------
            I   X (np.ndarray): The design matrix, with n rows of p features each.
            II  t (np.ndarray): The target vector, with n rows of p targets.
            III lam (float32): regularization parameter used to punish the weights in case of overfitting

        Returns:
        ------------
            No return value.

        """
        out_derivative = derivate(self.output_func)
        hidden_derivative = derivate(self.hidden_func)

        for i in range(len(self.weights) - 1, -1, -1):
            # delta terms for output
            if i == len(self.weights) - 1:
                # for multi-class classification
                if (
                    self.output_func.__name__ == "softmax"
                ):
                    delta_matrix = self.a_matrices[i + 1] - t
                # for single class classification
                else:
                    cost_func_derivative = grad(self.cost_func(t))
                    delta_matrix = out_derivative(
                        self.z_matrices[i + 1]
                    ) * cost_func_derivative(self.a_matrices[i + 1])

            # delta terms for hidden layer
            else:
                delta_matrix = (
                    self.weights[i + 1][1:, :] @ delta_matrix.T
                ).T * hidden_derivative(self.z_matrices[i + 1])

            # calculate gradient
            gradient_weights = self.a_matrices[i][:, 1:].T @ delta_matrix
            gradient_bias = npf.sum(delta_matrix, axis=0).reshape(
                1, delta_matrix.shape[1]
            )

            # regularization term
            gradient_weights += self.weights[i][1:, :] * lam

            # use scheduler
            update_matrix = npf.vstack(
                [
                    self.schedulers_bias[i].update_change(gradient_bias),
                    self.schedulers_weight[i].update_change(gradient_weights),
                ]
            )

            # update weights and bias
            self.weights[i] -= update_matrix

    def _accuracy(self, prediction: npf.ndarray, target: npf.ndarray):
        """
        Description:
        ------------
            Calculates accuracy of given prediction to target

        Parameters:
        ------------
            I   prediction (np.ndarray): vector of predicitons output network
                (1s and 0s in case of classification, and real numbers in case of regression)
            II  target (np.ndarray): vector of true values (What the network ideally should predict)

        Returns:
        ------------
            A floating point number representing the percentage of correctly classified instances.
        """
        assert prediction.size == target.size
        return npf.average((target == prediction))
    def _set_classification(self):
        """
        Description:
        ------------
            Decides if FFNN acts as classifier (True) og regressor (False),
            sets self.classification during init()
        """
        self.classification = False
        if (
            self.cost_func.__name__ == "CostLogReg"
            or self.cost_func.__name__ == "CostCrossEntropy"
        ):
            self.classification = True

    def _progress_bar(self, progression, **kwargs):
        """
        Description:
        ------------
            Displays progress of training
        """
        print_length = 40
        num_equals = int(progression * print_length)
        num_not = print_length - num_equals
        arrow = ">" if num_equals > 0 else ""
        bar = "[" + "=" * (num_equals - 1) + arrow + "-" * num_not + "]"
        perc_print = self._format(progression * 100, decimals=5)
        line = f"  {bar} {perc_print}% "

        for key in kwargs:
            if not npf.isnan(kwargs[key]):
                value = self._format(kwargs[key], decimals=4)
                line += f"| {key}: {value} "
        sys.stdout.write("\r" + line)
        sys.stdout.flush()
        return len(line)

    def _format(self, value, decimals=4):
        """
        Description:
        ------------
            Formats decimal numbers for progress bar
        """
        if value > 0:
            v = value
        elif value < 0:
            v = -10 * value
        else:
            v = 1
        n = 1 + math.floor(math.log10(v))
        if n >= decimals - 1:
            return str(round(value))
        return f"{value:.{decimals-n-1}f}"
    
    

def create_X(x, y, n):
    if len(x.shape) > 1:
        x = npf.ravel(x)
        y = npf.ravel(y)

    N = len(x)
    l = int((n + 1) * (n + 2) / 2)  # Number of elements in beta
    X = npf.ones((N, l))

    for i in range(1, n + 1):
        q = int((i) * (i + 1) / 2)
        for k in range(i + 1):
            X[:, q + k] = (x ** (i - k)) * (y**k)

    return X    

In [13]:
#This code is used to compute all training,test,bootrap,cross valdation MSE for all models variyng both polynomial
#degree and tunining paramter for Ridge and Lasso.


#import packages
#import numpy as np
import math
from sklearn.preprocessing import PolynomialFeatures, StandardScaler
from random import random, seed
from sklearn.metrics import mean_squared_error,r2_score,mean_absolute_error,mean_squared_log_error
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,PolynomialFeatures,MinMaxScaler
import math
from sklearn.pipeline import Pipeline
import pandas as pd
import imageio 
from sklearn.linear_model import LinearRegression, Ridge, Lasso, LassoLars
from sklearn.utils import shuffle


#set seed
npf.random.seed(1244)

#Import geographical image
terrain = imageio.v2.imread('SRTM_data_Norway_1.tif')
N = 1000

# Descretize the image
terrain = terrain[:N, :N]


#Sample 100 points from the image bu sampling x and y coordiante and then extracting the image pixel value 
sample_size=100
row = npf.random.choice(N ,sample_size, replace=False)
column=npf.random.choice(N , sample_size, replace=False)


samp=npf.vstack([row,column]).T


z=terrain[samp[:,0],samp[:,1]] 

#Min-Max scale on x,y and z
row=row.reshape(-1, 1)
scaler1 =MinMaxScaler()
scaler1.fit(row)
row=scaler1.transform(row).ravel()
        
column=column.reshape(-1, 1)
scaler2 =MinMaxScaler()
scaler2.fit(column)
column=scaler2.transform(column).ravel()
        

z=z.reshape(-1, 1)
scaler3 =MinMaxScaler()
scaler3.fit(z)
z=scaler3.transform(z).ravel()+0.5*npf.random.rand(sample_size)
print(z.shape)       
z = z.reshape(z.shape[0], 1)
poly_degree=3
X = create_X(row, column, poly_degree)
X_train,X_test,t_train,t_test=train_test_split(X,z,test_size=0.2)

print(X)

(100,)
[[1.00000000e+00 3.80380380e-02 3.26701571e-01 1.44689234e-03
  1.24270868e-02 1.06733916e-01 5.50369458e-05 4.72701999e-04
  4.05994877e-03 3.48701381e-02]
 [1.00000000e+00 6.82682683e-01 9.72774869e-01 4.66055645e-01
  6.64096557e-01 9.46290946e-01 3.18168118e-01 4.53367219e-01
  6.46016442e-01 9.20528051e-01]
 [1.00000000e+00 9.00900901e-03 2.90052356e-01 8.11622433e-05
  2.61308429e-03 8.41303692e-02 7.31191381e-07 2.35412999e-05
  7.57931254e-04 2.44022118e-02]
 [1.00000000e+00 5.20520521e-01 6.05235602e-01 2.70941612e-01
  3.15037551e-01 3.66310134e-01 1.41030669e-01 1.63983510e-01
  1.90671942e-01 2.21703935e-01]
 [1.00000000e+00 4.20420420e-02 9.26701571e-01 1.76753330e-03
  3.89604264e-02 8.58775801e-01 7.43107093e-05 1.63797588e-03
  3.61046883e-02 7.95828884e-01]
 [1.00000000e+00 9.61961962e-01 1.52879581e-01 9.25370816e-01
  1.47064342e-01 2.33721663e-02 8.90171526e-01 1.41470303e-01
  2.24831350e-02 3.57312700e-03]
 [1.00000000e+00 7.72772773e-01 1.87434555e-01 5.97

In [14]:
input_nodes = X_train.shape[1]
output_nodes = 1

linear_regression = FFNN((input_nodes,64,64,64,64,64, output_nodes), output_func=identity, cost_func=CostOLS, seed=2023)




scheduler = Constant(eta=1e-3)
scores = linear_regression.fit(X_train, t_train, scheduler)

linear_regression.reset_weights() # reset weights such that previous runs or reruns don't affect the weights

scores = linear_regression.fit(X_train, t_train, scheduler, lam=1e-4, epochs=1000)



Constant: Eta=0.001, Lambda=0
  [=======================================>] 100.0% | train_error: 0.0864 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0319 

In [15]:

from sklearn.metrics import mean_squared_error,r2_score
#for i in range(X_test.shape[1]):
y_hat=linear_regression.predict( X_test)

mean_squared_error(t_test,y_hat)


0.05473591405940085

In [16]:


from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import SGD
from keras.losses import MeanSquaredError, BinaryCrossentropy
from sklearn.metrics import r2_score
import numpy as np


class FFNN_tensorflow:
    def __init__(self, input_dim, output_dim, hidden_layers=(64, 32), hidden_activation='relu', output_activation=None, 
                 cost_function='mean_squared_error', learning_rate=0.01, regularization=None):
        self.input_dim = input_dim
        self.output_dim = output_dim
        self.hidden_layers = hidden_layers
        self.hidden_activation = hidden_activation
        self.output_activation = output_activation
        self.cost_function = cost_function
        self.learning_rate = learning_rate
        self.regularization = regularization
        self.model = self.build_model()

    def build_model(self):
        model = Sequential()
        model.add(Dense(self.hidden_layers[0], input_dim=self.input_dim, activation=self.hidden_activation))
        for layer_size in self.hidden_layers[1:]:
            model.add(Dense(layer_size, activation=self.hidden_activation))
        model.add(Dense(self.output_dim, activation=self.output_activation))

        optimizer = SGD(learning_rate=self.learning_rate)
        
        if self.cost_function == 'mean_squared_error':
            loss_function = MeanSquaredError()
        elif self.cost_function == 'r2_score':
            loss_function = self.r2_score_loss
        elif self.cost_function == 'binary_cross_entropy':
            loss_function = BinaryCrossentropy()

        if self.regularization == 'l1':
            regularizer = tf.keras.regularizers.l1()
        elif self.regularization == 'l2':
            regularizer = tf.keras.regularizers.l2()
        else:
            regularizer = None

        model.compile(loss=loss_function, optimizer=optimizer, metrics=['accuracy'], loss_weights=regularizer)
        return model

    def r2_score_loss(self, y_true, y_pred):
        return 1 - r2_score(y_true, y_pred)

    def fit(self, X, y, epochs=100, batch_size=None, validation_data=None):
        self.model.fit(X, y, epochs=epochs, batch_size=batch_size, validation_data=validation_data)

    def predict(self, X):
        return self.model.predict(X)

#Example usage:
#For regression task
input_dim = X_train.shape[1]
output_dim = 1
hidden_layers = (64, 32)
learning_rate = 0.01
epochs = 100
model = FFNN_tensorflow(input_dim=input_dim, output_dim=output_dim, hidden_layers=hidden_layers, learning_rate=learning_rate)
model.fit(X_train, t_train, epochs=epochs)
predictions = model.predict(X_test)



Epoch 1/100
3/3 [==============================] - 1s 9ms/step - loss: 0.5393 - accuracy: 0.0000e+00
Epoch 2/100
3/3 [==============================] - 0s 3ms/step - loss: 0.3746 - accuracy: 0.0000e+00
Epoch 3/100
3/3 [==============================] - 0s 5ms/step - loss: 0.2782 - accuracy: 0.0000e+00
Epoch 4/100
3/3 [==============================] - 0s 3ms/step - loss: 0.2149 - accuracy: 0.0000e+00
Epoch 5/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1708 - accuracy: 0.0000e+00
Epoch 6/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1415 - accuracy: 0.0000e+00
Epoch 7/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1215 - accuracy: 0.0000e+00
Epoch 8/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1056 - accuracy: 0.0000e+00
Epoch 9/100
3/3 [==============================] - 0s 3ms/step - loss: 0.0941 - accuracy: 0.0000e+00
Epoch 10/100
3/3 [==============================] - 0s 4ms/step - loss: 0.0867 - accuracy: 

In [17]:



t_scale=npf.mean(t_train)
# Bootstrap and KFold class definitions
class BootstrapKfold:
    def __init__(self):
        pass

    def bootstrap(self, n, function, degree, z, X_train, X_test, y_train, y_test, alpha):
        """
        Perform bootstrap resampling and calculate Cross-Validated Mean Squared Errors (MSE) for regression models.

        Parameters:
            n (int): Number of bootstrap samples.
            function (function): Regression function to be evaluated.
            degree (int): Polynomial degree for regression.
            z (array): Target values for regression.
            X_train (array): Training features.
            X_test (array): Testing features.
            y_train (array): Training target values.
            y_test (array): Testing target values.
            alpha (float): Regularization parameter (alpha) for Ridge and Lasso regression.

        Returns:
            float: Cross-validated mean training MSE.
            float: Cross-validated mean test MSE.
        """
        
        Boot_test_MSE = 0
        Boot_train_MSE = 0

        for i in range(n):
            indices = npf.random.choice(X_train.shape[0], size=z.shape[0], replace=True)
            X_boot = X_train[indices]
            y_boot = y_train[indices]

            train_MSE, test_MSE = function(degree, X_boot, X_test, y_boot, y_test, alpha)

            Boot_test_MSE += test_MSE
            Boot_train_MSE += train_MSE

        Boot_test_MSE /= n
        Boot_train_MSE /= n

        return Boot_train_MSE, Boot_test_MSE

    def kfold(self, K, function, degree, z,X,alpha):
        """
        Perform K-Fold cross-validation and calculate Mean Squared Errors (MSE) for regression models.

        Parameters:
            K (int): Number of folds.
            function (function): Regression function to be evaluated.
            degree (int): Polynomial degree for regression.
            z (array): Target values for regression.
            X_train (array): Training features.
            X_test (array): Testing features.
            y_train (array): Training target values.
            y_test (array): Testing target values.
            alpha (float): Regularization parameter (alpha) for Ridge and Lasso regression.

        Returns:
            float: Cross-validated mean training MSE.
            float: Cross-validated mean test MSE.
        """
        
        
       
      

        #shuffle data
        X=shuffle(X, random_state=0)
        z=shuffle(z, random_state=0)
        
        #indexes for k-fold boundaries
        fold_size = int(math.ceil(len(z) / K))
        
        #initialize accumulation variables
        CV_test_MSE = 0
        CV_train_MSE = 0

        for i in range(len(z)):
            
            test_start = i * fold_size
            test_end = min((i + 1) * fold_size, len(z))
            start_stop = npf.arange(test_start, test_end, 1)
            X_test_fold = X[start_stop]
            y_test_fold = z[start_stop]
            rest = npf.setdiff1d(npf.arange(z.shape[0]), start_stop)
            X_train_fold = X[rest]
            y_train_fold = z[rest]

            train_MSE, test_MSE = function(degree, X_train_fold, X_test_fold, y_train_fold, y_test_fold, alpha)

            CV_test_MSE += test_MSE
            CV_train_MSE += train_MSE

            if test_end == len(z):
                break

        CV_test_MSE /= K
        CV_train_MSE /= K

        return CV_train_MSE, CV_test_MSE

# RegressionClass definition
class RegressionClass:
    def __init__(self):
        pass
    
    def ols(self, degree, X_train, X_test, t_train, t_test, alpha):
        """
        Perform Ordinary Least Squares regression.

        Parameters:
            degree (int): Polynomial degree for regression.
            X_train (array): Training features.
            X_test (array): Testing features.
            y_train (array): Training target values.
            y_test (array): Testing target values.
            alpha (float): Regularization parameter (not used in OLS).

        Returns:
            float: Training MSE.
            float: Test MSE.
        """
        
        #create design matrices for test and training data
        pipeline = Pipeline([('poly', PolynomialFeatures(degree=degree, interaction_only=False, include_bias=False))
                            ])
        
        
        X_train = pipeline.fit_transform(X_train)
        X_test = pipeline.fit_transform(X_test)
        
        
        #Center the design matrices column wise with X_trains column means
        scaler =StandardScaler(with_std=False)
        scaler.fit(X_train)
        X_train=scaler.transform(X_train)
        X_test=scaler.transform(X_test)
        
        #Center y_train
        t_train = t_train- t_scale
        #compute optimal parameters the minimizes the least squares
        fit = npf.linalg.pinv(X_train.T @ X_train) @ (X_train).T @ t_train
        
        #fit the paramters to training and test design matrices
        y_hat_train = X_train @ fit
        
        #add intercept to get prediction on uncentered data
        y_hat_test = X_test @ fit+ t_scale
        #Compute the mean squares error
        mse_train_test = npf.array([mean_squared_error(t_train, y_hat_train), mean_squared_error(t_test, y_hat_test)])
        return mse_train_test

    def FFNN(self, degree, X_train, X_test, t_train, t_test, alpha):
        pipeline = Pipeline([('poly', PolynomialFeatures(degree=degree, interaction_only=False, include_bias=False))
                            ])
        
        
        X_train = pipeline.fit_transform(X_train)
        X_test = pipeline.fit_transform(X_test)
        
        
        #Center the design matrices column wise with X_trains column means
        scaler = StandardScaler(with_std=False)
        scaler.fit(X_train)
        X_train = scaler.transform(X_train)
        X_test = scaler.transform(X_test)
        
        input_nodes = X_train.shape[1]
        output_nodes = 1
        linear_regression = FFNN((input_nodes,64,64,64,64,64, output_nodes),hidden_func=sigmoid, output_func=identity, cost_func=CostOLS, seed=2023)




        scheduler =  Adam(eta=1e-4, rho=0.9, rho2=0.9999)
        scores = linear_regression.fit(X_train, t_train, scheduler,lam=alpha)

        linear_regression.reset_weights() # reset weights such that previous runs or reruns don't affect the weights

        scores = linear_regression.fit(X_train, t_train, scheduler, lam=1e-4, epochs=1000)
        predictions_train=linear_regression.predict( X_train)
        predictions_test=linear_regression.predict( X_test)
        MSE_result=npf.array([mean_squared_error(t_train,predictions_train),mean_squared_error(t_train,predictions_train)])
        return MSE_result 
    
        
    def FFNN_tensor_flow(self, degree, X_train, X_test, t_train, t_test, alpha):    
        pipeline = Pipeline([('poly', PolynomialFeatures(degree=degree, interaction_only=False, include_bias=False))
                            ])
        
        
        X_train = pipeline.fit_transform(X_train)
        X_test = pipeline.fit_transform(X_test)
        
        
        #Center the design matrices column wise with X_trains column means
        scaler =StandardScaler(with_std=False)
        scaler.fit(X_train)
        X_train=scaler.transform(X_train)
        X_test=scaler.transform(X_test)
        input_dim = X_train.shape[1]
        output_dim = 1
        model = FFNN_tensorflow(input_dim=input_dim, output_dim=output_dim, hidden_layers=hidden_layers, learning_rate=learning_rate,regularization=alpha)
        model.fit(X_train, t_train, epochs=epochs)
        predictions_train = model.predict(X_train)
        predictions_test = model.predict(X_test)
        MSE_result=npf.array([mean_squared_error(t_train,predictions_train),mean_squared_error(t_test,predictions_test)])
        return MSE_result 
    
class RunRegression(RegressionClass, BootstrapKfold):
    def __init__(self):
        self.regression_functions = {
            'ols': self.ols,
            'FFNN': self.FFNN,
            'FFNN_tensor_flow': self.FFNN_tensor_flow
        }

    def run(self, regression_type, alpha_values, degrees, X_train, X_test, y_train, y_test, use_bootstrap=False,
            use_kfold=False):
        """
        Run regression models with specified parameters.

        Parameters:
            regression_type (str): Type of regression ('ols', 'ridge', or 'lasso').
            alpha_values (list): List of alpha values for Ridge and Lasso regression.
            degrees (list): List of polynomial degrees for regression models.
            X_train (array): Training features.
            X_test (array): Testing features.
            y_train (array): Training target values.
            y_test (array): Testing target values.
            use_bootstrap (bool): Flag to indicate if bootstrap resampling should be performed.
            use_kfold (bool): Flag to indicate if K-Fold cross-validation should be performed.

        Returns:
            pandas.DataFrame: Dataframe containing regression results.
        """
        results = []
        #run for all polynomial complexities and tuning paramters defined
        for alpha in alpha_values:
            alpha_results = []

            for degree in degrees:
                mse_train_test = self.regression_functions[regression_type](degree, X_train, X_test, y_train, y_test,
                                                                            alpha)
                alpha_result = {
                    'alpha': alpha,
                    'degree': degree,
                    'mse_train': mse_train_test[0],
                    'mse_test': mse_train_test[1],
                }
                
                #include Bootstrap if condition is true
                if use_bootstrap:
                    cv_train_mse, cv_test_mse = self.bootstrap(100, self.regression_functions[regression_type],
                                                               degree, z, X_train, X_test, y_train, y_test, alpha)
                    alpha_result['bootstrap_train_mse'] = cv_train_mse
                    alpha_result['bootstrap_test_mse'] = cv_test_mse
                #Include 5-CV if condition is true
                if use_kfold:
                    cv_train_mse, cv_test_mse = self.kfold(5, self.regression_functions[regression_type],
                                                           degree, z, npf.column_stack((row, column)), alpha)
                    alpha_result['5cv_train_mse'] = cv_train_mse
                    alpha_result['5cv_test_mse'] = cv_test_mse
                 
                #Include 10-CV if condition is true
            
                if use_kfold:
                    cv_train_mse, cv_test_mse = self.kfold(10, self.regression_functions[regression_type],
                                                           degree, z, npf.column_stack((row, column)), alpha)
                    alpha_result['10cv_train_mse'] = cv_train_mse
                    alpha_result['10cv_test_mse'] = cv_test_mse

                alpha_results.append(alpha_result)

            results.extend(alpha_results)

        result_df = pd.DataFrame(results)
        return result_df
    

# Create an instance of the RunRegression class
regression_instance = RegressionClass()
run_regression_instance = RunRegression()

# Define the alpha values and degrees
alpha_values = [0.00001, 0.00002, 0.00004, 0.0005]
degrees = list(range(1,6))

# Specify the type of regression ('ols', 'ridge', or 'lasso')
regression_type = 'FFNN'  # Change to 'lasso' or 'ols' to run other regressions

# Call the run method to perform the specified regression
result_df_ridge = run_regression_instance.run(regression_type, alpha_values,degrees,X_train, X_test, t_train, t_test,use_bootstrap=False, use_kfold=True)


result_df_ridge

regression_type = 'ols'  # OLS regression

# Set alpha to 0 when calling the run method for OLS
result_df_ols = run_regression_instance.run(regression_type, [0], degrees,  X_train, X_test, t_train, t_test,use_bootstrap=False, use_kfold=True)

result_df_ols


regression_type = 'FFNN_tensor_flow'  # Lasso regression

result_df_lasso = run_regression_instance.run(regression_type,alpha_values, degrees, X_train, X_test, t_train, t_test,use_bootstrap=False, use_kfold=True)

result_df_lasso


from IPython.display import display

# Assuming you have multiple DataFrames df1, df2, df3
display(result_df_ridge)
display(result_df_ols)
display(result_df_lasso)

Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.152 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0445 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.137 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0410 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.138 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0491 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.148 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0497 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.159 Constant: Eta=0.001, Lambda=0

  [=======================================>] 100.0% | train_error: 0.0484 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.127 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0444 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.130 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0467 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.125 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0518 Constant: Eta=0.001, Lambda=1e-05
  [=======================================>] 100.0% | train_error: 0.117 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0472 Constant: Eta=0.001, Lambda=2e-05
  [=========================

  [=======================================>] 100.0% | train_error: 0.0581 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.277 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0559 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.208 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0469 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.248 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0503 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.234 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0434 Constant: Eta=0.001, Lambda=2e-05
  [=========================

  [=======================================>] 100.0% | train_error: 0.0576 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.145 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0579 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.130 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0567 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.126 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0565 Constant: Eta=0.001, Lambda=2e-05
  [=======================================>] 100.0% | train_error: 0.134 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0484 Constant: Eta=0.001, Lambda=2e-05
  [=========================

  [=======================================>] 100.0% | train_error: 0.0587 Constant: Eta=0.001, Lambda=4e-05
  [=======================================>] 100.0% | train_error: 0.134 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0535 Constant: Eta=0.001, Lambda=4e-05
  [=======================================>] 100.0% | train_error: 0.128 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0499 Constant: Eta=0.001, Lambda=4e-05
  [=======================================>] 100.0% | train_error: 0.392 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0438 Constant: Eta=0.001, Lambda=4e-05
  [=======================================>] 100.0% | train_error: 0.266 Constant: Eta=0.001, Lambda=0.0001
  [=======================================>] 100.0% | train_error: 0.0581 Constant: Eta=0.001, Lambda=4e-05
  [=========================

...

Epoch 1/100
3/3 [==============================] - 0s 4ms/step - loss: 0.4419 - accuracy: 0.0000e+00
Epoch 2/100
3/3 [==============================] - 0s 4ms/step - loss: 0.3651 - accuracy: 0.0000e+00
Epoch 3/100
3/3 [==============================] - 0s 5ms/step - loss: 0.3039 - accuracy: 0.0000e+00
Epoch 4/100
3/3 [==============================] - 0s 4ms/step - loss: 0.2549 - accuracy: 0.0000e+00
Epoch 5/100
3/3 [==============================] - 0s 4ms/step - loss: 0.2159 - accuracy: 0.0000e+00
Epoch 6/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1847 - accuracy: 0.0000e+00
Epoch 7/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1605 - accuracy: 0.0000e+00
Epoch 8/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1414 - accuracy: 0.0000e+00
Epoch 9/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1261 - accuracy: 0.0000e+00
Epoch 10/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1142 - accuracy: 

Epoch 1/100
3/3 [==============================] - 0s 3ms/step - loss: 0.4258 - accuracy: 0.0000e+00
Epoch 2/100
3/3 [==============================] - 0s 4ms/step - loss: 0.3437 - accuracy: 0.0000e+00
Epoch 3/100
3/3 [==============================] - 0s 4ms/step - loss: 0.2788 - accuracy: 0.0000e+00
Epoch 4/100
3/3 [==============================] - 0s 4ms/step - loss: 0.2276 - accuracy: 0.0000e+00
Epoch 5/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1868 - accuracy: 0.0000e+00
Epoch 6/100
3/3 [==============================] - 0s 4ms/step - loss: 0.1559 - accuracy: 0.0000e+00
Epoch 7/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1318 - accuracy: 0.0000e+00
Epoch 8/100
3/3 [==============================] - 0s 3ms/step - loss: 0.1134 - accuracy: 0.0000e+00
Epoch 9/100
3/3 [==============================] - 0s 4ms/step - loss: 0.0994 - accuracy: 0.0000e+00
Epoch 10/100
3/3 [==============================] - 0s 3ms/step - loss: 0.0889 - accuracy: 

alpha  degree  mse_train  mse_test  5cv_train_mse  5cv_test_mse  \
0   0.00001       1   0.055752  0.055752       0.063413      0.063413   
1   0.00001       2   0.107061  0.107061       0.070858      0.070858   
2   0.00001       3   0.120939  0.120939       0.057358      0.057358   
3   0.00001       4   0.126853  0.126853       0.084650      0.084650   
4   0.00001       5   0.155479  0.155479       0.064370      0.064370   
5   0.00002       1   0.055752  0.055752       0.063413      0.063413   
6   0.00002       2   0.107061  0.107061       0.070858      0.070858   
7   0.00002       3   0.120939  0.120939       0.057358      0.057358   
8   0.00002       4   0.126853  0.126853       0.084650      0.084650   
9   0.00002       5   0.155479  0.155479       0.064370      0.064370   
10  0.00004       1   0.055752  0.055752       0.063413      0.063413   
11  0.00004       2   0.107061  0.107061       0.070858      0.070858   
12  0.00004       3   0.120939  0.120939       0.057358      0.057358   
13  0.00004       4   0.126853  0.126853       0.084650      0.084650   
14  0.00004       5   0.155479  0.155479       0.064370      0.064370   
15  0.00050       1   0.055752  0.055752       0.063413      0.063413   
16  0.00050       2   0.107061  0.107061       0.070858      0.070858   
17  0.00050       3   0.120939  0.120939       0.057358      0.057358   
18  0.00050       4   0.126853  0.126853       0.084650      0.084650   
19  0.00050       5   0.155479  0.155479       0.064370      0.064370   

    10cv_train_mse  10cv_test_mse  
0         0.057972       0.057972  
1         0.071358       0.071358  
2         0.057747       0.057747  
3         0.084616       0.084616  
4         0.063279       0.063279  
5         0.057972       0.057972  
6         0.071358       0.071358  
7         0.057747       0.057747  
8         0.084616       0.084616  
9         0.063279       0.063279  
10        0.057972       0.057972  
11        0.071358       0.071358  
12        0.057747       0.057747  
13        0.084616       0.084616  
14        0.063279       0.063279  
15        0.057972       0.057972  
16        0.071358       0.071358  
17        0.057747       0.057747  
18        0.084616       0.084616  
19        0.063279       0.063279

alpha  degree  mse_train      mse_test  5cv_train_mse  5cv_test_mse  \
0      0       1   0.035026      0.082119       0.059221      0.061775   
1      0       2   0.021184      0.185573       0.045827      0.051558   
2      0       3   0.010392     20.050917       0.040887      0.050714   
3      0       4   0.008099    603.896234       0.030146      0.047456   
4      0       5   0.007118  39685.336011       0.026528      0.073444   

   10cv_train_mse  10cv_test_mse  
0        0.059306       0.062387  
1        0.046096       0.050906  
2        0.041289       0.051752  
3        0.030619       0.049840  
4        0.027416       0.079353

alpha  degree  mse_train  mse_test  5cv_train_mse  5cv_test_mse  \
0   0.00001       1   0.045072  0.080021       0.055305      0.055137   
1   0.00001       2   0.037948  0.074132       0.051650      0.059629   
2   0.00001       3   0.029908  0.082917       0.047916      0.051606   
3   0.00001       4   0.031027  0.086768       0.046201      0.051190   
4   0.00001       5   0.026189  0.101850       0.047523      0.055198   
5   0.00002       1   0.040707  0.080918       0.053272      0.057679   
6   0.00002       2   0.032397  0.087437       0.048543      0.049785   
7   0.00002       3   0.035326  0.083067       0.047838      0.052717   
8   0.00002       4   0.026130  0.109350       0.046758      0.052868   
9   0.00002       5   0.028162  0.100511       0.046614      0.049350   
10  0.00004       1   0.041158  0.075914       0.052154      0.055914   
11  0.00004       2   0.033059  0.084251       0.048381      0.055180   
12  0.00004       3   0.031432  0.083422       0.048869      0.055832   
13  0.00004       4   0.028921  0.097853       0.047599      0.051966   
14  0.00004       5   0.028966  0.104548       0.047868      0.056046   
15  0.00050       1   0.038473  0.074085       0.054845      0.060899   
16  0.00050       2   0.035732  0.074231       0.048538      0.053679   
17  0.00050       3   0.029705  0.083565       0.047824      0.054047   
18  0.00050       4   0.029048  0.087273       0.048674      0.056311   
19  0.00050       5   0.027319  0.104056       0.045577      0.054193   

    10cv_train_mse  10cv_test_mse  
0         0.054382       0.055750  
1         0.047613       0.053943  
2         0.047991       0.055472  
3         0.049384       0.055792  
4         0.046419       0.052910  
5         0.052056       0.056665  
6         0.048972       0.056176  
7         0.047513       0.054694  
8         0.047632       0.051881  
9         0.049765       0.057456  
10        0.055169       0.057774  
11        0.049560       0.052794  
12        0.046898       0.054865  
13        0.050163       0.056248  
14        0.047679       0.054189  
15        0.053467       0.059821  
16        0.047393       0.051977  
17        0.048419       0.052624  
18        0.048254       0.055087  
19        0.047173       0.054001

In [18]:
display(result_df_ridge)
display(result_df_lasso)

alpha  degree  mse_train  mse_test  5cv_train_mse  5cv_test_mse  \
0   0.00001       1   0.055752  0.055752       0.063413      0.063413   
1   0.00001       2   0.107061  0.107061       0.070858      0.070858   
2   0.00001       3   0.120939  0.120939       0.057358      0.057358   
3   0.00001       4   0.126853  0.126853       0.084650      0.084650   
4   0.00001       5   0.155479  0.155479       0.064370      0.064370   
5   0.00002       1   0.055752  0.055752       0.063413      0.063413   
6   0.00002       2   0.107061  0.107061       0.070858      0.070858   
7   0.00002       3   0.120939  0.120939       0.057358      0.057358   
8   0.00002       4   0.126853  0.126853       0.084650      0.084650   
9   0.00002       5   0.155479  0.155479       0.064370      0.064370   
10  0.00004       1   0.055752  0.055752       0.063413      0.063413   
11  0.00004       2   0.107061  0.107061       0.070858      0.070858   
12  0.00004       3   0.120939  0.120939       0.057358      0.057358   
13  0.00004       4   0.126853  0.126853       0.084650      0.084650   
14  0.00004       5   0.155479  0.155479       0.064370      0.064370   
15  0.00050       1   0.055752  0.055752       0.063413      0.063413   
16  0.00050       2   0.107061  0.107061       0.070858      0.070858   
17  0.00050       3   0.120939  0.120939       0.057358      0.057358   
18  0.00050       4   0.126853  0.126853       0.084650      0.084650   
19  0.00050       5   0.155479  0.155479       0.064370      0.064370   

    10cv_train_mse  10cv_test_mse  
0         0.057972       0.057972  
1         0.071358       0.071358  
2         0.057747       0.057747  
3         0.084616       0.084616  
4         0.063279       0.063279  
5         0.057972       0.057972  
6         0.071358       0.071358  
7         0.057747       0.057747  
8         0.084616       0.084616  
9         0.063279       0.063279  
10        0.057972       0.057972  
11        0.071358       0.071358  
12        0.057747       0.057747  
13        0.084616       0.084616  
14        0.063279       0.063279  
15        0.057972       0.057972  
16        0.071358       0.071358  
17        0.057747       0.057747  
18        0.084616       0.084616  
19        0.063279       0.063279

alpha  degree  mse_train  mse_test  5cv_train_mse  5cv_test_mse  \
0   0.00001       1   0.045072  0.080021       0.055305      0.055137   
1   0.00001       2   0.037948  0.074132       0.051650      0.059629   
2   0.00001       3   0.029908  0.082917       0.047916      0.051606   
3   0.00001       4   0.031027  0.086768       0.046201      0.051190   
4   0.00001       5   0.026189  0.101850       0.047523      0.055198   
5   0.00002       1   0.040707  0.080918       0.053272      0.057679   
6   0.00002       2   0.032397  0.087437       0.048543      0.049785   
7   0.00002       3   0.035326  0.083067       0.047838      0.052717   
8   0.00002       4   0.026130  0.109350       0.046758      0.052868   
9   0.00002       5   0.028162  0.100511       0.046614      0.049350   
10  0.00004       1   0.041158  0.075914       0.052154      0.055914   
11  0.00004       2   0.033059  0.084251       0.048381      0.055180   
12  0.00004       3   0.031432  0.083422       0.048869      0.055832   
13  0.00004       4   0.028921  0.097853       0.047599      0.051966   
14  0.00004       5   0.028966  0.104548       0.047868      0.056046   
15  0.00050       1   0.038473  0.074085       0.054845      0.060899   
16  0.00050       2   0.035732  0.074231       0.048538      0.053679   
17  0.00050       3   0.029705  0.083565       0.047824      0.054047   
18  0.00050       4   0.029048  0.087273       0.048674      0.056311   
19  0.00050       5   0.027319  0.104056       0.045577      0.054193   

    10cv_train_mse  10cv_test_mse  
0         0.054382       0.055750  
1         0.047613       0.053943  
2         0.047991       0.055472  
3         0.049384       0.055792  
4         0.046419       0.052910  
5         0.052056       0.056665  
6         0.048972       0.056176  
7         0.047513       0.054694  
8         0.047632       0.051881  
9         0.049765       0.057456  
10        0.055169       0.057774  
11        0.049560       0.052794  
12        0.046898       0.054865  
13        0.050163       0.056248  
14        0.047679       0.054189  
15        0.053467       0.059821  
16        0.047393       0.051977  
17        0.048419       0.052624  
18        0.048254       0.055087  
19        0.047173       0.054001